In [1]:
import pandas as pd
import numpy as np
import warnings

warnings.filterwarnings("ignore")

data = pd.read_csv("model_df.csv", index_col=0)
data['date'] = pd.to_datetime(data['Date'])
data = data.sort_values(by="Date", ascending=True)
data['home_1h_score'] = data['Home 1H Points']
data['away_1h_score'] = data['Away 1H Points']
data['home_score'] = data['Home Full Points']
data['away_score'] = data['Away Full Points']
data['total'] = data['home_score'] + data['away_score']
data['home_2h_score'] = data['home_score'] - data['home_1h_score']
data['away_2h_score'] = data['away_score'] - data['away_1h_score']
data['home_team'] = data['Team_home']
data['away_team'] = data['Team_away']
data['margin'] = data['home_score'] - data['away_score']

In [ ]:
data["home_opp_score_rank"] = data["Rk_away"] - data['home_score']
data['away_opp_score_rank'] = data['Rk_home'] - data['away_score']
data['home_sos'] = data['Rk_away']
data['away_sos'] = data['Rk_home']

In [ ]:
# Melt data to unify home and away records with opponent scores
home_df = data[['date', 'home_team', 'home_score', 'away_score', 'home_sos', "home_opp_score_rank"]].rename(columns={
    'home_team': 'team', 'home_score': 'score', 'away_score': 'opponent_score', 'home_sos': 'sos', "home_opp_score_rank": "opp_score_rank"
})
away_df = data[['date', 'away_team', 'away_score', 'home_score','away_sos', "away_opp_score_rank"]].rename(columns={
    'away_team': 'team', 'away_score': 'score', 'home_score': 'opponent_score','away_sos': 'sos', "away_opp_score_rank": "opp_score_rank"
})
games = pd.concat([home_df, away_df])
games.sort_values(by=['team', 'date'], inplace=True)

# Define the rolling windows
rolling_windows = [1, 3, 7]

# Calculate rolling averages for each window and store as separate columns
for window in rolling_windows:
    games[f'rolling_avg_score_{window}'] = games.groupby('team')['score'].shift().rolling(window=window, min_periods=1).mean()
    games[f'rolling_avg_score_allowed_{window}'] = games.groupby('team')['opponent_score'].shift().rolling(window=window, min_periods=1).mean()
    games[f'rolling_sos_{window}'] = games.groupby('team')['sos'].shift().rolling(window=window, min_periods=1).mean()
    games[f'rolling_opp_score_rank_{window}'] = games.groupby('team')['opp_score_rank'].shift().rolling(window=window, min_periods=1).mean()


games['days_since_last_game'] = games.groupby('team')['date'].diff().dt.days

# Keep only necessary columns
columns_to_keep = ['date', 'team', 'days_since_last_game'] + \
                  [f'rolling_avg_score_{w}' for w in rolling_windows] + \
                  [f'rolling_sos_{w}' for w in rolling_windows] + \
                  [f'rolling_avg_score_allowed_{w}' for w in rolling_windows] + \
                  [f'rolling_opp_score_rank_{w}' for w in rolling_windows]
games = games[columns_to_keep]

# Merge rolling features back to the original data on home and away team sides
# First, join for home team
data = data.merge(
    games.rename(columns={
        'team': 'home_team',
        **{f'rolling_avg_score_{w}': f'home_rolling_avg_score_{w}' for w in rolling_windows},
        **{f'rolling_sos_{w}': f'home_rolling_sos_{w}' for w in rolling_windows},
        **{f'rolling_opp_score_rank_{w}': f'home_rolling_opp_score_rank_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_allowed_{w}': f'home_rolling_avg_score_allowed_{w}' for w in rolling_windows},
        'days_since_last_game': 'home_days_since_last_game'
    }),
    on=['date', 'home_team'],
    how='left'
)

# Then, join for away team
data = data.merge(
    games.rename(columns={
        'team': 'away_team',
        **{f'rolling_avg_score_{w}': f'away_rolling_avg_score_{w}' for w in rolling_windows},
        **{f'rolling_sos_{w}': f'away_rolling_sos_{w}' for w in rolling_windows},
        **{f'rolling_opp_score_rank_{w}': f'away_rolling_opp_score_rank_{w}' for w in rolling_windows},
        **{f'rolling_avg_score_allowed_{w}': f'away_rolling_avg_score_allowed_{w}' for w in rolling_windows},
        'days_since_last_game': 'away_days_since_last_game'
    }),
    on=['date', 'away_team'],
    how='left'
)

In [ ]:
df = data.dropna()

In [2]:
df = pd.read_csv("train.csv")

In [3]:
df['margin'] = df['home_score'] - df['away_score']

In [ ]:
import optuna
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from sklearn.preprocessing import LabelEncoder
import lightgbm as lgb
import joblib
import os
import pandas as pd

os.makedirs("lgb_models", exist_ok=True)

# Define threshold values for high and low outliers for training the Isolation Forest
high_outlier_thresholds = {'home_score': 91, 'away_score': 78, 'total': 167}
low_outlier_thresholds = {'home_score': 56, 'away_score': 52, 'total': 118}

# Specify the features and target column for each target
for target_column in ['home_score', 'away_score', 'total', 'margin']:
    categorical_columns = ['Conf_home', 'Conf_away']  # Update to actual categorical columns

    # Prepare data
    model_df = df[[target_column, 'Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]
    
    # Encode categorical columns
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df[cat_col] = le.fit_transform(df[cat_col])

    # Initialize and fit Isolation Forest
    iso_forest = IsolationForest(contamination=0.1, random_state=42)
    iso_forest.fit(model_df.drop([target_column, 'Date'], axis=1))
    
    # Add outlier score as a feature
    model_df['outlier_score'] = iso_forest.decision_function(model_df.drop([target_column, 'Date'], axis=1))
    # Ensure the dataframe is sorted by the "date" column
    model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
    model_df = model_df.sort_values(by='date')

    # Define the split ratio
    test_ratio = 0.2  # 20% of the data will be used for testing
    split_index = int(len(model_df) * (1 - test_ratio))

    # Split data into training and testing sets
    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    # Separate features and target
    X_train = train_data.drop(columns=['date', 'Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['date', 'Date', target_column])
    y_test = test_data[target_column]

    # Define Optuna objective function for LightGBM
    def objective_lgb(trial):
        param = {
            'objective': 'regression',
            'metric': 'rmse',
            'boosting_type': 'gbdt',
            'max_depth': trial.suggest_int('max_depth', -1, 8),
            'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.3),
            'n_estimators': trial.suggest_int('n_estimators', 100, 1500),
            'num_leaves': trial.suggest_int('num_leaves', 20, 150),
            'min_child_samples': trial.suggest_int('min_child_samples', 5, 50),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
        }
        
        # Convert training and testing sets to lightgbm.Dataset
        train_data = lgb.Dataset(X_train, label=y_train)
        valid_data = lgb.Dataset(X_test, label=y_test)
        
        # Train LightGBM model with early stopping
        model = lgb.train(
            params=param,
            train_set=train_data,
            valid_sets=[train_data, valid_data],
            valid_names=["train", "valid"]        )
        
        # Use best iteration for prediction
        y_pred = model.predict(X_test, num_iteration=model.best_iteration)
        rmse = mean_squared_error(y_test, y_pred, squared=False)
        return rmse



    # Optimize LightGBM with Optuna
    study_lgb = optuna.create_study(direction='minimize')
    study_lgb.optimize(objective_lgb, n_trials=50)
    print(f"Best LightGBM parameters for {target_column}: {study_lgb.best_params}")

    # Train the best LightGBM model with the optimized parameters
    best_lgb = lgb.LGBMRegressor(**study_lgb.best_params)
    best_lgb.fit(X_train, y_train)
    y_pred_lgb = best_lgb.predict(X_test)

    # Save the final best model for this target column
    best_model_filename = f"lgb_models/{target_column}_best_model.joblib"
    joblib.dump(best_lgb, best_model_filename)

    # Define a function to calculate and display metrics
    def display_metrics(y_true, y_pred, model_name):
        r2 = r2_score(y_true, y_pred)
        mae = mean_absolute_error(y_true, y_pred)
        rmse = mean_squared_error(y_true, y_pred, squared=False)
        print(f"{model_name} R^2: {r2:.4f}")
        print(f"{model_name} MAE: {mae:.4f}")
        print(f"{model_name} RMSE: {rmse:.4f}")

    # Display metrics for the LightGBM model
    display_metrics(y_test, y_pred_lgb, "LightGBM with Outlier Score Feature")

In [4]:
import optuna
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from sklearn.preprocessing import LabelEncoder
import lightgbm as lgb
import joblib
import os
import pandas as pd

os.makedirs("lgb_models", exist_ok=True)

# Define thresholds for capping target values
target_outlier_thresholds = {
    'home_score': {'low': 50, 'high': 100},
    'away_score': {'low': 50, 'high': 100},
    'total': {'low': 110, 'high': 180},
    'margin': {'low': -30, 'high': 30},
}

# Specify the features and target column for each target
for target_column in ['margin', 'total', 'away_score', 'home_score']:
    categorical_columns = ['Conf_home', 'Conf_away']  # Update to actual categorical columns

    # Prepare data
    model_df = df[[target_column, 'Date','Rk_home','Conf_home', 'AdjEM_home', 'AdjO_home',
       'AdjO_Rk_home', 'AdjD_home', 'AdjD_Rk_home', 'AdjT_home',
       'AdjT_Rk_home', 'Rk_rolling_1_home',
       'AdjEM_rolling_1_home', 'AdjO_rolling_1_home',
       'AdjO_Rk_rolling_1_home', 'AdjD_rolling_1_home',
       'AdjD_Rk_rolling_1_home', 'AdjT_rolling_1_home',
       'AdjT_Rk_rolling_1_home', 'Rk_rolling_3_home',
       'AdjEM_rolling_3_home', 'AdjO_rolling_3_home',
       'AdjO_Rk_rolling_3_home', 'AdjD_rolling_3_home',
       'AdjD_Rk_rolling_3_home', 'AdjT_rolling_3_home',
       'AdjT_Rk_rolling_3_home', 'Rk_rolling_5_home',
       'AdjEM_rolling_5_home', 'AdjO_rolling_5_home',
       'AdjO_Rk_rolling_5_home', 'AdjD_rolling_5_home',
       'AdjD_Rk_rolling_5_home', 'AdjT_rolling_5_home',
       'AdjT_Rk_rolling_5_home', 'Rk_rolling_10_home',
       'AdjEM_rolling_10_home', 'AdjO_rolling_10_home',
       'AdjO_Rk_rolling_10_home', 'AdjD_rolling_10_home',
       'AdjD_Rk_rolling_10_home', 'AdjT_rolling_10_home',
       'AdjT_Rk_rolling_10_home', 'Rk_rolling_20_home',
       'AdjEM_rolling_20_home', 'AdjO_rolling_20_home',
       'AdjO_Rk_rolling_20_home', 'AdjD_rolling_20_home',
       'AdjD_Rk_rolling_20_home', 'AdjT_rolling_20_home',
       'AdjT_Rk_rolling_20_home', 'Rk_away', 'Conf_away',
       'AdjEM_away', 'AdjO_away', 'AdjO_Rk_away', 'AdjD_away',
       'AdjD_Rk_away', 'AdjT_away', 'AdjT_Rk_away',
       'Rk_rolling_1_away', 'AdjEM_rolling_1_away', 'AdjO_rolling_1_away',
       'AdjO_Rk_rolling_1_away', 'AdjD_rolling_1_away',
       'AdjD_Rk_rolling_1_away', 'AdjT_rolling_1_away',
       'AdjT_Rk_rolling_1_away', 'Rk_rolling_3_away',
       'AdjEM_rolling_3_away', 'AdjO_rolling_3_away',
       'AdjO_Rk_rolling_3_away', 'AdjD_rolling_3_away',
       'AdjD_Rk_rolling_3_away', 'AdjT_rolling_3_away',
       'AdjT_Rk_rolling_3_away', 'Rk_rolling_5_away',
       'AdjEM_rolling_5_away', 'AdjO_rolling_5_away',
       'AdjO_Rk_rolling_5_away', 'AdjD_rolling_5_away',
       'AdjD_Rk_rolling_5_away', 'AdjT_rolling_5_away',
       'AdjT_Rk_rolling_5_away', 'Rk_rolling_10_away',
       'AdjEM_rolling_10_away', 'AdjO_rolling_10_away',
       'AdjO_Rk_rolling_10_away', 'AdjD_rolling_10_away',
       'AdjD_Rk_rolling_10_away', 'AdjT_rolling_10_away',
       'AdjT_Rk_rolling_10_away', 'Rk_rolling_20_away',
       'AdjEM_rolling_20_away', 'AdjO_rolling_20_away',
       'AdjO_Rk_rolling_20_away', 'AdjD_rolling_20_away',
       'AdjD_Rk_rolling_20_away', 'AdjT_rolling_20_away',
       'AdjT_Rk_rolling_20_away',  'home_sos',
       'away_sos', 'home_days_since_last_game',
       'home_rolling_avg_score_1', 'home_rolling_avg_score_3',
       'home_rolling_avg_score_7', 'home_rolling_sos_1',
       'home_rolling_sos_3', 'home_rolling_sos_7',
       'home_rolling_avg_score_allowed_1',
       'home_rolling_avg_score_allowed_3',
       'home_rolling_avg_score_allowed_7',
       'home_rolling_opp_score_rank_1', 'home_rolling_opp_score_rank_3',
       'home_rolling_opp_score_rank_7', 'away_days_since_last_game',
       'away_rolling_avg_score_1', 'away_rolling_avg_score_3',
       'away_rolling_avg_score_7', 'away_rolling_sos_1',
       'away_rolling_sos_3', 'away_rolling_sos_7',
       'away_rolling_avg_score_allowed_1',
       'away_rolling_avg_score_allowed_3',
       'away_rolling_avg_score_allowed_7',
       'away_rolling_opp_score_rank_1', 'away_rolling_opp_score_rank_3',
       'away_rolling_opp_score_rank_7']]

    # Handle outliers in the target column using capping
    low_threshold = target_outlier_thresholds[target_column]['low']
    high_threshold = target_outlier_thresholds[target_column]['high']
    model_df[target_column] = model_df[target_column].clip(lower=low_threshold, upper=high_threshold)

    # Encode categorical columns
    for cat_col in categorical_columns:
        le = LabelEncoder()
        model_df[cat_col] = le.fit_transform(df[cat_col])

    # Ensure the dataframe is sorted by the "date" column
    model_df['date'] = pd.to_datetime(df['Date'])  # Convert to datetime if not already
    model_df = model_df.sort_values(by='date')

    # Define the split ratio
    test_ratio = 0.2  # 20% of the data will be used for testing
    split_index = int(len(model_df) * (1 - test_ratio))

    # Split data into training and testing sets
    train_data = model_df.iloc[:split_index]
    test_data = model_df.iloc[split_index:]

    # Separate features and target
    X_train = train_data.drop(columns=['date', 'Date', target_column])
    y_train = train_data[target_column]

    X_test = test_data.drop(columns=['date', 'Date', target_column])
    y_test = test_data[target_column]

    # Define Optuna objective function for LightGBM
    def objective_lgb(trial):
        param = {
            'objective': 'regression',
            'metric': 'rmse',
            'boosting_type': 'gbdt',
            'max_depth': trial.suggest_int('max_depth', -1, 8),
            'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 0.3),
            'n_estimators': trial.suggest_int('n_estimators', 100, 1500),
            'num_leaves': trial.suggest_int('num_leaves', 20, 150),
            'min_child_samples': trial.suggest_int('min_child_samples', 5, 50),
            'subsample': trial.suggest_float('subsample', 0.5, 1.0),
            'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
            'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 5.0),
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 5.0),
        }
        
        # Convert training and testing sets to lightgbm.Dataset
        train_data = lgb.Dataset(X_train, label=y_train)
        valid_data = lgb.Dataset(X_test, label=y_test)
        
        # Train LightGBM model with early stopping
        model = lgb.train(
            params=param,
            train_set=train_data,
            valid_sets=[train_data, valid_data],
            valid_names=["train", "valid"],
        )
        
        # Use best iteration for prediction
        y_pred = model.predict(X_test, num_iteration=model.best_iteration)
        rmse = mean_squared_error(y_test, y_pred, squared=False)
        return rmse

    # Optimize LightGBM with Optuna
    study_lgb = optuna.create_study(direction='minimize')
    study_lgb.optimize(objective_lgb, n_trials=50)
    print(f"Best LightGBM parameters for {target_column}: {study_lgb.best_params}")

    # Train the best LightGBM model with the optimized parameters
    best_lgb = lgb.LGBMRegressor(**study_lgb.best_params)
    best_lgb.fit(X_train, y_train)
    y_pred_lgb = best_lgb.predict(X_test)

    # # Save the final best model for this target column
    # best_model_filename = f"lgb_models/{target_column}_best_model.joblib"
    # joblib.dump(best_lgb, best_model_filename)

    # Define a function to calculate and display metrics
    def display_metrics(y_true, y_pred, model_name):
        r2 = r2_score(y_true, y_pred)
        mae = mean_absolute_error(y_true, y_pred)
        rmse = mean_squared_error(y_true, y_pred, squared=False)
        print(f"{model_name} R^2: {r2:.4f}")
        print(f"{model_name} MAE: {mae:.4f}")
        print(f"{model_name} RMSE: {rmse:.4f}")

    # Display metrics for the LightGBM model
    display_metrics(y_test, y_pred_lgb, "LightGBM with Capped Targets")

[I 2024-11-20 10:34:11,824] A new study created in memory with name: no-name-0ee6e468-1415-435b-ab1b-8e815c26ff41


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013606 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191


[I 2024-11-20 10:35:18,114] Trial 0 finished with value: 11.35964641688846 and parameters: {'max_depth': -1, 'learning_rate': 0.032955157252366044, 'n_estimators': 1479, 'num_leaves': 139, 'min_child_samples': 38, 'subsample': 0.6947795095061342, 'colsample_bytree': 0.9964349538407773, 'reg_alpha': 1.4961588308222868, 'reg_lambda': 1.5838270607004457}. Best is trial 0 with value: 11.35964641688846.


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013965 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score -0.004191


[I 2024-11-20 10:35:32,182] Trial 1 finished with value: 11.353952083092603 and parameters: {'max_depth': -1, 'learning_rate': 0.08102028693747998, 'n_estimators': 550, 'num_leaves': 81, 'min_child_samples': 10, 'subsample': 0.9007977604362787, 'colsample_bytree': 0.8062878012741002, 'reg_alpha': 2.5866491386826382, 'reg_lambda': 0.9310532606711336}. Best is trial 1 with value: 11.353952083092603.


...

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013065 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score 70.017838
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf


[I 2024-11-20 11:08:54,956] Trial 48 finished with value: 9.890197911722128 and parameters: {'max_depth': 2, 'learning_rate': 0.03562841358062643, 'n_estimators': 1130, 'num_leaves': 107, 'min_child_samples': 7, 'subsample': 0.5657341283965708, 'colsample_bytree': 0.6784069140439772, 'reg_alpha': 4.127523234791698, 'reg_lambda': 0.3812432764059618}. Best is trial 42 with value: 9.879797951859771.


[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.013117 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score 70.017838


[I 2024-11-20 11:09:15,103] Trial 49 finished with value: 10.145377121686108 and parameters: {'max_depth': 0, 'learning_rate': 0.09841853894677172, 'n_estimators': 768, 'num_leaves': 73, 'min_child_samples': 25, 'subsample': 0.595487029863014, 'colsample_bytree': 0.76648048406116, 'reg_alpha': 4.604443724157495, 'reg_lambda': 1.668087153675108}. Best is trial 42 with value: 9.879797951859771.


Best LightGBM parameters for home_score: {'max_depth': 3, 'learning_rate': 0.035653275381749054, 'n_estimators': 878, 'num_leaves': 106, 'min_child_samples': 18, 'subsample': 0.5039703808848308, 'colsample_bytree': 0.7577216676249743, 'reg_alpha': 4.366498144719926, 'reg_lambda': 0.761964652521025}
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.024130 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30540
[LightGBM] [Info] Number of data points in the train set: 55835, number of used features: 126
[LightGBM] [Info] Start training from score 70.017838
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive